# Analyse de l'incidence de la varicelle

In [14]:
import isoweek
import pandas as pd

Les données sont téléchargées en local, on peut donc les lire grâce à la bibliothèque pandas

In [8]:
data_path = "inc-7-PAY.csv"

raw_data = pd.read_csv(data_path, skiprows=1)
raw_data

week  indicator    inc  inc_low  inc_up  inc100  inc100_low  \
0     202443          7   2701      725    4677       4           1   
1     202442          7   2659     1260    4058       4           2   
2     202441          7   2035      381    3689       3           1   
3     202440          7   2125      725    3525       3           1   
4     202439          7   2898     1333    4463       4           2   
5     202438          7    751        0    1513       1           0   
6     202437          7    916       28    1804       1           0   
7     202436          7   2235      870    3600       3           1   
8     202435          7   1620      285    2955       2           0   
9     202434          7   2560      622    4498       4           1   
10    202433          7   1971      536    3406       3           1   
11    202432          7   4399     1944    6854       7           3   
12    202431          7   4500     2213    6787       7           4   
13    202430          7   7004     4278    9730      11           7   
14    202429          7   9270     6303   12237      14          10   
15    202428          7   9364     6498   12230      14          10   
16    202427          7  10247     7090   13404      15          10   
17    202426          7  14368    10399   18337      22          16   
18    202425          7  11174     8039   14309      17          12   
19    202424          7  12621     9357   15885      19          14   
20    202423          7  14657    11339   17975      22          17   
21    202422          7  11628     8361   14895      17          12   
22    202421          7   9701     6851   12551      15          11   
23    202420          7  13661    10209   17113      20          15   
24    202419          7  10083     6413   13753      15           9   
25    202418          7  13438     9514   17362      20          14   
26    202417          7  15303    11219   19387      23          17   
27    202416          7  18138    13540   22736      27          20   
28    202415          7  24929    17315   32543      37          26   
29    202414          7  16181    12544   19818      24          19   
...      ...        ...    ...      ...     ...     ...         ...   
1739  199126          7  17608    11304   23912      31          20   
1740  199125          7  16169    10700   21638      28          18   
1741  199124          7  16171    10071   22271      28          17   
1742  199123          7  11947     7671   16223      21          13   
1743  199122          7  15452     9953   20951      27          17   
1744  199121          7  14903     8975   20831      26          16   
1745  199120          7  19053    12742   25364      34          23   
1746  199119          7  16739    11246   22232      29          19   
1747  199118          7  21385    13882   28888      38          25   
1748  199117          7  13462     8877   18047      24          16   
1749  199116          7  14857    10068   19646      26          18   
1750  199115          7  13975     9781   18169      25          18   
1751  199114          7  12265     7684   16846      22          14   
1752  199113          7   9567     6041   13093      17          11   
1753  199112          7  10864     7331   14397      19          13   
1754  199111          7  15574    11184   19964      27          19   
1755  199110          7  16643    11372   21914      29          20   
1756  199109          7  13741     8780   18702      24          15   
1757  199108          7  13289     8813   17765      23          15   
1758  199107          7  12337     8077   16597      22          15   
1759  199106          7  10877     7013   14741      19          12   
1760  199105          7  10442     6544   14340      18          11   
1761  199104          7   7913     4563   11263      14           8   
1762  199103          7  15387    10484   20290      27          18   
1763  199102          7  16277  

Regardons si certaines lignes sont vides

In [9]:
raw_data[raw_data.isnull().any(axis=1)]

Empty DataFrame
Columns: [week, indicator, inc, inc_low, inc_up, inc100, inc100_low, inc100_up, geo_insee, geo_name]
Index: []

Il n'y a pas de données manquantes

On convertit maintenant les dates

In [20]:
def convert_week(year_and_week_int):
    year_and_week_str = str(year_and_week_int)
    year = int(year_and_week_str[:4])
    week = int(year_and_week_str[4:])
    w = isoweek.Week(year, week)
    return pd.Period(w.day(0), 'W')

raw_data['period'] = [convert_week(yw) for yw in raw_data['week']]

Trions les données par ordre chronologique

In [21]:
sorted_data = raw_data.set_index('period').sort_index()

In [23]:
sorted_data.head()

week  indicator    inc  inc_low  inc_up  inc100  \
period                                                                     
1990-12-03/1990-12-09  199049          7   1143        0    2610       2   
1990-12-10/1990-12-16  199050          7  11079     6660   15498      20   
1990-12-17/1990-12-23  199051          7  19080    13807   24353      34   
1990-12-24/1990-12-30  199052          7  19375    13295   25455      34   
1990-12-31/1991-01-06  199101          7  15565    10271   20859      27   

                       inc100_low  inc100_up geo_insee geo_name  
period                                                           
1990-12-03/1990-12-09           0          5        FR   France  
1990-12-10/1990-12-16          12         28        FR   France  
1990-12-17/1990-12-23          25         43        FR   France  
1990-12-24/1990-12-30          23         45        FR   France  
1990-12-31/1991-01-06          18         36        FR   France

Nous vérifions maintenant la cohérence des données, il ne doit pas y avoir d'écart d'une période à une autre

In [22]:
periods = sorted_data.index
for p1, p2 in zip(periods[:-1], periods[1:]):
    delta = p2.to_timestamp() - p1.end_time
    if delta > pd.Timedelta('1s'):
        print(p1, p2)

Rien ne s'affiche, les périodes semblent cohérentes.

Les données commencent en décembre 1990. Comme notre date référence est le 1er septembre, nous commençons l'analyse en septembre 1991

In [26]:
first_septembre_week = [pd.Period(pd.Timestamp(y, 9, 1), 'W')
                     for y in range(1991,
                                    sorted_data.index[-1].year)]

Nous calculons maintenant l'incidence chaque année en vérifiant qu'il y ait toujours 51 ou 52 semaines par années

In [27]:
year = []
yearly_incidence = []
for week1, week2 in zip(first_septembre_week[:-1],
                        first_septembre_week[1:]):
    one_year = sorted_data['inc'][week1:week2-1]
    assert abs(len(one_year)-52) < 2
    yearly_incidence.append(one_year.sum())
    year.append(week2.year)
yearly_incidence = pd.Series(data=yearly_incidence, index=year)

Nous cherchons maintenant les années durant lesquelles l'épidémie était la plus forte et la plus faible, c'est à dire les années durant lesquelles l'incidence était respectivement la plus élevée et la plus petite.

In [34]:
yearly_incidence.idxmax()

2009

In [35]:
yearly_incidence.idxmin()

2020

L'épidémie était la plus forte en 2009 et la plus faible en 2020